In [ ]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, AutoModelForSeq2SeqLM
from sentence_transformers import SentenceTransformer, util
from itertools import combinations
import numpy as np
import json
from tqdm import tqdm

In [ ]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 16.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 16.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 19.3 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [ ]:
from datasets import load_dataset

In [ ]:
from tqdm import tqdm

In [ ]:
dataset = load_dataset("BeIR/scifact", "corpus")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/14.0k [00:00<?, ?B/s]

scifact.py:   0%|          | 0.00/1.66k [00:00<?, ?B/s]

0000.parquet:   0%|          | 0.00/4.58M [00:00<?, ?B/s]

Generating corpus split:   0%|          | 0/5183 [00:00<?, ? examples/s]

In [ ]:
dataset

DatasetDict({
    corpus: Dataset({
        features: ['_id', 'title', 'text'],
        num_rows: 5183
    })
})

In [ ]:
dataset_q = load_dataset("BeIR/scifact", "queries")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/14.0k [00:00<?, ?B/s]

scifact.py:   0%|          | 0.00/1.66k [00:00<?, ?B/s]

queries/queries/0000.parquet:   0%|          | 0.00/67.5k [00:00<?, ?B/s]

Generating queries split:   0%|          | 0/1109 [00:00<?, ? examples/s]

In [ ]:
dataset_q

DatasetDict({
    queries: Dataset({
        features: ['_id', 'title', 'text'],
        num_rows: 1109
    })
})

In [ ]:
dataset_qrel = load_dataset("BeIR/scifact-qrels", split="test")

README.md:   0%|          | 0.00/14.0k [00:00<?, ?B/s]

train.tsv:   0%|          | 0.00/14.5k [00:00<?, ?B/s]

test.tsv:   0%|          | 0.00/5.39k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/919 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/339 [00:00<?, ? examples/s]

In [ ]:
dataset_qrel

Dataset({
    features: ['query-id', 'corpus-id', 'score'],
    num_rows: 339
})

In [ ]:
from collections import defaultdict

# Initialize a defaultdict to store query-doc pairs
qrels = defaultdict(dict)

# Iterate over the dataset and populate the dictionary
for qrel in dataset_qrel:
    qrels[str(qrel["query-id"])][str(qrel["corpus-id"])] = qrel["score"]

# Convert defaultdict back to a regular dictionary if needed
qrels = dict(qrels)

In [ ]:
qrels

{'1': {'31715818': 1},
 '3': {'14717500': 1},
 '5': {'13734012': 1},
 '13': {'1606628': 1},
 '36': {'5152028': 1, '11705328': 1},
 '42': {'18174210': 1},
 '48': {'13734012': 1},
 '49': {'5953485': 1},
 '50': {'12580014': 1},
 '51': {'45638119': 1},
 '53': {'45638119': 1},
 '54': {'49556906': 1},
 '56': {'4709641': 1},
 '57': {'4709641': 1},
 '70': {'5956380': 1, '4414547': 1},
 '72': {'6076903': 1},
 '75': {'4387784': 1},
 '94': {'1215116': 1},
 '99': {'18810195': 1},
 '100': {'4381486': 1},
 '113': {'6157837': 1},
 '115': {'33872649': 1},
 '118': {'6372244': 1},
 '124': {'4883040': 1},
 '127': {'21598000': 1},
 '128': {'8290953': 1},
 '129': {'27768226': 1},
 '130': {'27768226': 1},
 '132': {'7975937': 1},
 '133': {'38485364': 1,
  '6969753': 1,
  '17934082': 1,
  '16280642': 1,
  '12640810': 1},
 '137': {'26016929': 1},
 '141': {'6955746': 1, '14437255': 1},
 '142': {'10582939': 1},
 '143': {'10582939': 1},
 '146': {'10582939': 1},
 '148': {'1084345': 1},
 '163': {'18872233': 1},
 '1

In [ ]:
len(qrels)

300

In [ ]:
print(f"Number of query-document pairs: {len(qrels)}")

Number of query-document pairs: 300


In [ ]:
queries = {query["_id"]: query["text"] for query in dataset_q["queries"]}

In [ ]:
print(f"Number of queries: {len(queries)}")


Number of queries: 1109


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:

file_path = "/content/drive/MyDrive/646Project/sharedfiles/document_generated_queries_withdiversequeries_flan-t5-large_scifact.json"

with open(file_path, "r") as file:
  data = json.load(file)


In [ ]:
document_pseudo_queries = data

In [ ]:
import random

In [ ]:
# Example dictionaries
# dictionary_1 = qrels
# dictionary_2 = document_pseudo_queries
# dictionary_3 = queries

# dictionary_1 = {
#     "query_id_1": {"doc_id_1": 0.8, "doc_id_2": 0.6},
#     "query_id_2": {"doc_id_3": 0.9, "doc_id_4": 0.7},
# }

# dictionary_2 = {
#     "doc_id_1": ["query_1", "query_2"],
#     "doc_id_2": ["query_3", "query_4", "query_5"],
#     "doc_id_3": ["query_6"],
#     "doc_id_4": ["query_7", "query_8"],
# }

# dictionary_3 = {
#     "query_id_1": "input_query_1",
#     "query_id_2": "input_query_2",
# }

# Step 1: Create a mapping from input query to related queries
input_output_mapping = {}

for query_id, doc_scores in qrels.items():
    input_query = queries[query_id]
    related_queries = set()  # Use a set to avoid duplicate queries

    # For each document associated with the query_id, find related queries
    for doc_id in doc_scores.keys():
        if doc_id in document_pseudo_queries:
            related_queries.update(document_pseudo_queries[doc_id])  # Add all queries for this doc_id

    if len(related_queries) > 20:
        related_queries = set(random.sample(list(related_queries), 20))

    # Step 2: Combine related queries into a single comprehensive query
    # For simplicity, let's combine the related queries into one text, which could be enhanced further
    comprehensive_query = " ".join(list(related_queries))  # Combine queries into a single string


    # Store the input-output pair
    input_output_mapping[input_query] = comprehensive_query

# Step 3: Print the mapping (training data pairs)
# for input_query, comprehensive_query in input_output_mapping.items():
#     print(f"Input Query: {input_query}")
#     print(f"Output Query: {comprehensive_query}")


In [ ]:
for input_query, comprehensive_query in input_output_mapping.items():
    print(f"Input Query: {input_query}")
    print(f"Output Query: {comprehensive_query}")
    break

Input Query: 0-dimensional biomaterials show inductive properties.
Output Query: Which nanotechnologies are used to track stem cells? What is the most common use of nanotechnology?


In [ ]:
data = [{"input_query": input_query, "comprehensive_query": comprehensive_query}
        for input_query, comprehensive_query in input_output_mapping.items()]

In [ ]:
from datasets import Dataset

In [ ]:
len_input_output_mapping= len(data)
eval_data = data[len_input_output_mapping-10:len_input_output_mapping]
train_data = data[100:len_input_output_mapping-10]

# Convert the data into Hugging Face Dataset format
train_dataset = Dataset.from_list(train_data)
eval_dataset = Dataset.from_list(eval_data)

In [ ]:
print("Train dataset:")
print(train_dataset[:2])  # Show first 2 examples
print("Eval dataset:")
print(eval_dataset[:2])

Train dataset:
{'input_query': ['Healthcare delivery efficiency in crowded delivery centers is impaired by improving structural, logistical, and interpersonal elements.', 'Helminths interfere with immune system control of macrophages activated by IL-4 favor Mycobacterium tuberculosis replication.'], 'comprehensive_query': ['How much more money is needed to meet the WHO targets? What is the estimated global financial resources necessary to scale up antiretroviral therapy in  How many people could receive ART in 2020? What was the estimated annual resource needed for scaling up ART? What is the estimated financial resources needed?', 'Which T-helper 1 cytokines are involved in regulating autophagy in Does inhibition of starvation-induced autophagy in macrophages by IL Which cytokines inhibit autophagy? IFN-gamma is induced through what mechanism in macrophages? Does inhibition of iFN-gamma trigger autophagy in macrophages']}
Eval dataset:
{'input_query': ['Varenicline monotherapy is more

In [ ]:
from transformers import T5Tokenizer, T5ForConditionalGeneration, Trainer, TrainingArguments

# Load pre-trained model and tokenizer
tokenizer = T5Tokenizer.from_pretrained("t5-small")
model = T5ForConditionalGeneration.from_pretrained("t5-small")






tokenizer_config.json:   0%|          | 0.00/2.32k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565


config.json:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/242M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

In [ ]:
# Prepare dataset for training
def tokenize_function(batch):
    inputs = tokenizer(batch['input_query'], padding=True, truncation=True, max_length=512)
    outputs = tokenizer(batch['comprehensive_query'], padding=True, truncation=True, max_length=512)
    inputs['labels'] = outputs['input_ids']
    return inputs

In [ ]:
tokenized_train = train_dataset.map(tokenize_function, batched=True)
tokenized_eval = eval_dataset.map(tokenize_function, batched=True)

Map:   0%|          | 0/190 [00:00<?, ? examples/s]

Map:   0%|          | 0/10 [00:00<?, ? examples/s]

In [ ]:
# Assuming tokenized_datasets is prepared
training_args = TrainingArguments(
    output_dir="./results",
    evaluation_strategy="steps",
    num_train_epochs=3,
    per_device_train_batch_size=8,
    save_steps=10,
    save_total_limit=2,
)


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1568: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_train,
    eval_dataset=tokenized_eval,
    tokenizer=tokenizer,
)

<ipython-input-37-55974d6f33b0>:1: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


In [ ]:
trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.48.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.


TrainOutput(global_step=72, training_loss=4.505697038438585, metrics={'train_runtime': 92.0444, 'train_samples_per_second': 6.193, 'train_steps_per_second': 0.782, 'total_flos': 9944450334720.0, 'train_loss': 4.505697038438585, 'epoch': 3.0})

In [ ]:
model_save_path = "/content/drive/MyDrive/646Project/sharedfiles/t5_small_finetuned_test_scifact_2/"

# Save model and tokenizer
model.save_pretrained(model_save_path)
tokenizer.save_pretrained(model_save_path)

print(f"Model and tokenizer saved to {model_save_path}")

Model and tokenizer saved to /content/drive/MyDrive/646Project/sharedfiles/t5_small_finetuned_test_scifact_2/


In [ ]:
model_save_path = "/content/drive/MyDrive/646Project/sharedfiles/t5_small_finetuned_test_scifact_2/"

In [ ]:
from transformers import T5Tokenizer, T5ForConditionalGeneration

# Load the fine-tuned model and tokenizer
new_model = T5ForConditionalGeneration.from_pretrained(model_save_path)
new_tokenizer = T5Tokenizer.from_pretrained(model_save_path)  # Use the correct tokenizer

In [ ]:
test_data = data[:100]


In [ ]:
test_data[0]

{'input_query': '0-dimensional biomaterials show inductive properties.',
 'comprehensive_query': 'Which nanotechnologies are used to track stem cells? What is the most common use of nanotechnology?'}

In [ ]:
test_data[1]

{'input_query': '1,000 genomes project enables mapping of genetic sequence variation consisting of rare variants with larger penetrance effects than common variants.',
 'comprehensive_query': 'What are the two possible explanations for common variants being associated with diseases and traits found in What do they propose for a synthetic explanation for GWAS findings? What are the main conclusions? What is the name of the study they are describing? What does the study imply for the interpretation of GWAS findings?'}

In [ ]:
# test_data_refined = [{"input_query": input["input_query"] + "?"}
for input in test_data:
      print(input['input_query'])
      break


0-dimensional biomaterials show inductive properties.


In [ ]:
test_data_refined = [{"input_query": input['input_query']} for input in test_data]  # Add '?' to each query to make it a complete question


In [ ]:
test_data_refined

[{'input_query': '0-dimensional biomaterials show inductive properties.'},
 {'input_query': '1,000 genomes project enables mapping of genetic sequence variation consisting of rare variants with larger penetrance effects than common variants.'},
 {'input_query': '1/2000 in UK have abnormal PrP positivity.'},
 {'input_query': '5% of perinatal mortality is due to low birth weight.'},
 {'input_query': 'A deficiency of vitamin B12 increases blood levels of homocysteine.'},
 {'input_query': 'A high microerythrocyte count raises vulnerability to severe anemia in homozygous alpha (+)- thalassemia trait subjects.'},
 {'input_query': 'A total of 1,000 people in the UK are asymptomatic carriers of vCJD infection.'},
 {'input_query': 'ADAR1 binds to Dicer to cleave pre-miRNA.'},
 {'input_query': 'AIRE is expressed in some skin tumors.'},
 {'input_query': 'ALDH1 expression is associated with better breast cancer outcomes.'},
 {'input_query': 'ALDH1 expression is associated with poorer prognosis in 

In [ ]:
from tqdm import tqdm

In [ ]:


# Example test dataset (a list of input queries)
# test_data = [
#     {"input_query": "Does statin use reduce breast cancer mortality?"},
#     {"input_query": "How does methylmercury affect the nervous system?"},
#     {"input_query": "Does inositol hexaphosphate modulate neutrophils?"}
# ]

# Function to predict the comprehensive query
def predict_comprehensive_query(test_data_refined):

    # device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    # new_model.to(device)
    # tokenizer.to(device)

    predictions = []
    # test_data_refined_short = list(test_data_refined)[:2]
    for item in tqdm(test_data_refined):
        input_query = item["input_query"]

        # Tokenize the input query
        inputs = new_tokenizer(input_query, return_tensors="pt", padding=True, truncation=True, max_length=512)

        # Generate predictions using the model
        # with torch.no_grad():  # Disable gradient calculation for inference
        output_ids = new_model.generate(inputs["input_ids"], max_length=512, num_beams=4, early_stopping=True)

        # Decode the generated token IDs back to text
        predicted_query = new_tokenizer.decode(output_ids[0], skip_special_tokens=True)
        predictions.append(predicted_query)
        # break

    return predictions




In [ ]:
# Get predictions for the test data
predictions = predict_comprehensive_query(test_data_refined)

100%|██████████| 100/100 [41:13<00:00, 24.74s/it]


In [ ]:
queries_dict = list(qrels.items())[:100]

In [ ]:
# Model names
generative_model_name = "google/flan-t5-large"
similarity_model_name = "all-mpnet-base-v2"
chunk_size=500
overlap=0
threshold=0.8

In [ ]:
similarity_model = SentenceTransformer(similarity_model_name)

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/571 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/363 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [ ]:
def calculate_similarity_score(user_pseudo_query, document_pseudo_queries, similarity_model):
    """
    Calculate the similarity score for a query-document pair.

    Parameters:
    - query: The user query (string).
    - document_pseudo_queries: List of pseudo-queries for the document.
    - similarity_model: Preloaded Sentence Transformer model.

    Returns:
    - max_similarity: Maximum similarity score between query and pseudo-queries.
    """
    # Compute embeddings for the query and pseudo-queries
    # query_embedding = similarity_model.encode(user_pseudo_query, convert_to_tensor=True)
    # # pseudo_query_embeddings = similarity_model.encode(document_pseudo_queries, convert_to_tensor=True)

    # # Compute cosine similarity scores
    # similarity_scores = util.cos_sim(query_embedding, document_pseudo_queries)
    device = "cuda" if torch.cuda.is_available() else "cpu"

    similarity_model_gpu = similarity_model.to(device)

    # Compute embedding for the query on the specified device
    query_embedding = similarity_model_gpu.encode(
        user_pseudo_query,
        convert_to_tensor=True,
        device=device
    )

    if query_embedding.dim() == 1:
        query_embedding = query_embedding.unsqueeze(0)

    # Ensure pseudo-query embeddings are also on the same device
    document_pseudo_queries = document_pseudo_queries.to(device)
    # print(query_embedding.shape)
    # print(document_pseudo_queries.shape)

    # Compute cosine similarity scores
    similarity_scores = util.cos_sim(query_embedding, document_pseudo_queries)

    # Find the maximum similarity score
    max_similarity = torch.max(similarity_scores).item()
    return max_similarity



In [ ]:
def rank_documents_by_query(query, document_pseudo_queries_embeddings, similarity_model):
    """
    Rank documents based on the similarity of their pseudo-queries to the query.

    Parameters:
    - query: The user query (string).
    - document_queries_dict: Dictionary where keys are document IDs and values are lists of pseudo-queries.
    - similarity_model: Preloaded Sentence Transformer model.

    Returns:
    - ranked_scores: List of tuples (document_id, score) sorted by descending scores.
    """
    document_scores = {}
    for doc_id, pseudo_queries_embeddings in document_pseudo_queries_embeddings.items():
        # print(doc_id)
        # print(pseudo_queries)
        # print("yoo")
        score = calculate_similarity_score(query, pseudo_queries_embeddings, similarity_model)
        document_scores[doc_id] = score

    # Sort documents by scores in descending order
    ranked_scores = sorted(document_scores.items(), key=lambda x: x[1], reverse=True)
    return ranked_scores

In [ ]:
# queries_dict = list(qrels.items())[:2]
test_dict = {}
document_pseudo_queries_embeddings={}
device = "cuda" if torch.cuda.is_available() else "cpu"
similarity_model_gpu = similarity_model.to(device)

for doc_id, pseudo_queries in tqdm(document_pseudo_queries.items()):
  # print(pseudo_queries)
  # print(len(pseudo_queries))
  pseudo_query_embeddings = similarity_model_gpu.encode(pseudo_queries, convert_to_tensor=True, device = device)
  document_pseudo_queries_embeddings[doc_id] = pseudo_query_embeddings
  # # print(doc_id)
  # print(pseudo_query_embeddings[0])
  # print(len(pseudo_query_embeddings))
  # # print(document_pseudo_queries_embeddings)
  # break



100%|██████████| 5183/5183 [01:26<00:00, 59.85it/s]


In [ ]:
qrel_pseudo ={}
index=0
for query_id, doc_score in tqdm(queries_dict):

  user_pseudo_query =predictions[index]
  qrel_pseudo[str(query_id)]=user_pseudo_query
  # user_pseudo_query = queries[str(query_id)]
  doc_rank_for_query = rank_documents_by_query(user_pseudo_query, document_pseudo_queries_embeddings, similarity_model)
  # print(type(doc_rank_for_query))
  test_dict[query_id]={}
  index+=1
  for doc_id, score in doc_rank_for_query:
    test_dict[query_id][doc_id] = float(score)


100%|██████████| 100/100 [2:21:18<00:00, 84.79s/it]


In [ ]:
!pip install pytrec_eval

  Preparing metadata (setup.py) ... done
  Created wheel for pytrec_eval: filename=pytrec_eval-0.5-cp310-cp310-linux_x86_64.whl size=308215 sha256=8e97c7d3d2332a5971af0d56a2b715770396ec8fa4a43c9c3d6e95f3161e8299
  Stored in directory: /root/.cache/pip/wheels/51/3a/cd/dcc1ddfc763987d5cb237165d8ac249aa98a23ab90f67317a8
Successfully built pytrec_eval


In [ ]:
import pytrec_eval

In [ ]:
qrels

{'1': {'31715818': 1.0},
 '3': {'14717500': 1.0},
 '5': {'13734012': 1.0},
 '13': {'1606628': 1.0},
 '36': {'5152028': 1.0, '11705328': 1.0},
 '42': {'18174210': 1.0},
 '48': {'13734012': 1.0},
 '49': {'5953485': 1.0},
 '50': {'12580014': 1.0},
 '51': {'45638119': 1.0},
 '53': {'45638119': 1.0},
 '54': {'49556906': 1.0},
 '56': {'4709641': 1.0},
 '57': {'4709641': 1.0},
 '70': {'5956380': 1.0, '4414547': 1.0},
 '72': {'6076903': 1.0},
 '75': {'4387784': 1.0},
 '94': {'1215116': 1.0},
 '99': {'18810195': 1.0},
 '100': {'4381486': 1.0},
 '113': {'6157837': 1.0},
 '115': {'33872649': 1.0},
 '118': {'6372244': 1.0},
 '124': {'4883040': 1.0},
 '127': {'21598000': 1.0},
 '128': {'8290953': 1.0},
 '129': {'27768226': 1.0},
 '130': {'27768226': 1.0},
 '132': {'7975937': 1.0},
 '133': {'38485364': 1.0,
  '6969753': 1.0,
  '17934082': 1.0,
  '16280642': 1.0,
  '12640810': 1.0},
 '137': {'26016929': 1.0},
 '141': {'6955746': 1.0, '14437255': 1.0},
 '142': {'10582939': 1.0},
 '143': {'10582939': 1

In [ ]:
test_dict

{'1': {'5855168': 0.20527055859565735,
  '86217760': 0.20109857618808746,
  '25799020': 0.1987840235233307,
  '4231060': 0.19564346969127655,
  '4942718': 0.1938372403383255,
  '3770726': 0.1938372254371643,
  '7451607': 0.1938372254371643,
  '18361917': 0.1938372254371643,
  '21141798': 0.1938372254371643,
  '33796570': 0.1938372254371643,
  '54440': 0.1938372105360031,
  '13123189': 0.1938372105360031,
  '25950264': 0.1938372105360031,
  '15286783': 0.19383719563484192,
  '30507607': 0.19383716583251953,
  '34445160': 0.19355829060077667,
  '7260461': 0.1907346397638321,
  '40412980': 0.18725766241550446,
  '15282056': 0.1863364279270172,
  '15803282': 0.18474438786506653,
  '1836154': 0.1832830309867859,
  '3155731': 0.18288856744766235,
  '9704467': 0.17722384631633759,
  '8318286': 0.17657653987407684,
  '19419439': 0.17657653987407684,
  '46565968': 0.1728183925151825,
  '7137057': 0.17093244194984436,
  '26798867': 0.16866838932037354,
  '26474812': 0.1661502718925476,
  '139164

In [ ]:
top_n = 10
top_documents = {}
for query_id, doc_scores in test_dict.items():
  # Directly take the top N documents (already sorted)
  top_documents[query_id] = dict(list(doc_scores.items())[:top_n])

In [ ]:
evaluator = pytrec_eval.RelevanceEvaluator(qrels, {'P.3,5,10', 'recall.3,5,10', 'ndcg_cut.3,5,10', 'map_cut.3,5,10'})
result = evaluator.evaluate(top_documents)
print(result)
metrics = ['P','ndcg_cut', 'recall', 'map_cut']
cutoffs = [3,5,10]
scores = {f'{metric}_{cutoff}': 0 for metric in metrics for cutoff in cutoffs}
for key in result:
  for metric in metrics:
    for cutoff in cutoffs:
      scores[f'{metric}_{cutoff}'] += result[key][f'{metric}_{cutoff}']
run_length = len(test_dict)
for score in scores:
  scores[score] /= run_length

{'1': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, '3': {'P_3': 0.0, 'P_5': 0.2, 'P_10': 0.1, 'recall_3': 0.0, 'recall_5': 1.0, 'recall_10': 1.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.43067655807339306, 'ndcg_cut_10': 0.43067655807339306, 'map_cut_3': 0.0, 'map_cut_5': 0.25, 'map_cut_10': 0.25}, '5': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, '13': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5': 0.0, 'ndcg_cut_10': 0.0, 'map_cut_3': 0.0, 'map_cut_5': 0.0, 'map_cut_10': 0.0}, '36': {'P_3': 0.0, 'P_5': 0.0, 'P_10': 0.0, 'recall_3': 0.0, 'recall_5': 0.0, 'recall_10': 0.0, 'ndcg_cut_3': 0.0, 'ndcg_cut_5':

In [ ]:
scores

{'P_3': 0.019999999999999997,
 'P_5': 0.018,
 'P_10': 0.011,
 'ndcg_cut_3': 0.05630929753571458,
 'ndcg_cut_5': 0.06879135676952786,
 'ndcg_cut_10': 0.07550807740846537,
 'recall_3': 0.06,
 'recall_5': 0.09,
 'recall_10': 0.11,
 'map_cut_3': 0.055,
 'map_cut_5': 0.062,
 'map_cut_10': 0.06491666666666668}

In [ ]:
import json
with open("/content/drive/MyDrive/646Project/sharedfiles/qrel_pseudo_t5smallpart2finetuned_scifact", "w") as json_file:
  json.dump(qrel_pseudo, json_file, indent=4)

In [ ]:
test_data[0]['input_query']

'Do Cholesterol Statin Drugs Cause Breast Cancer?'

In [ ]:
test_data[1]['input_query']

'Exploiting Autophagy to Live Longer'

In [ ]:
predictions

['Die Medikamente mit Cholesterol-Statinen tragen zu Brustkrebs bei?',
 'Exploiting Autophagy to Live Longer Live, Exploiting Autophagy, Exploiting Autophagy, Exploiting Autophagy to Live Longer Live.']

In [ ]:
# test_data

In [ ]:
# Print the predicted comprehensive queries
for input_query, predicted_query in zip([item["input_query"] for item in test_data], predictions):
    print(f"Input Query: {input_query}")
    print(f"Predicted Comprehensive Query: {predicted_query}")
    print("-" * 50)